In [1]:
import os,sys
import tensorflow as tf
sys.path.append('/home/tanmay/JHU/project/deep-mediation/manuscript/code/deep-mediation/src')
import auxiliaryfunctions
import statsmodels.api as sm
import statsmodels.formula.api as smf
import seaborn as sns
import numpy as np
from scipy.stats import zscore,norm
from keras.callbacks import EarlyStopping
import matplotlib.pyplot as plt
import os
import pandas as pd
import random as python_random

from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error,make_scorer,mean_absolute_error,r2_score

from keras import backend as K

from tensorflow.keras.callbacks import LearningRateScheduler, ModelCheckpoint, EarlyStopping
from keras.optimizers import Adam, SGD

In [2]:
np.random.seed(123)
python_random.seed(123)
tf.random.set_seed(1234)

early_stopping = True
epochs = 1000
batch_size = 32
use_dynamic_LR=False
algo = 'deep' #options are [svr,shallow,deep] 
patience = 20
result_path = '/home/tanmay/JHU/project/deep-mediation/manuscript/code/deep-mediation/results/simulation-3'
num_subs = [100,500,1000]
num_iters = 20
num_runs = 100
new_shape = [28,28]

In [3]:
def create_empty_df(num_runs,num_iters):
    # Creates an empty dataFrame
    a = np.empty((num_runs,num_iters))
    a[:] = np.nan
    dataFrame = None
    parameters = ['alpha0', 'beta0','alpha','beta','gamma']
    for params in parameters:
        iter = ['iter_'+str(i) for i in range(num_iters)]
        pdindex = pd.MultiIndex.from_product([[params], iter],
                                             names=['parameters', 'runs']) 
        frame = pd.DataFrame(a, columns = pdindex,index = range(0,num_runs))
        dataFrame = pd.concat([dataFrame,frame],axis=1)
    return dataFrame

def simulate_mediation(df,M,params_df,model,algo,num_subs,batch_size,epochs,tune,n,n_runs,iterations):
    """
    """
    early_stopping=True
    # Initialize z with some phi
    print("Using intial random model parameters")
    z = model.predict(M) 
    try:
        z = np.concatenate(z)
    except:
        pass
    
    for i in range(0,iterations):
        print('Starting iteration... %s'%(i+1))
        #Check for sign change
        if np.corrcoef(z,df.Y)[0,1] < 0 :
            z = z*(-1)
        # Check for scaling
        z= zscore(z)

        lm = smf.ols(formula='z ~ X', data=df).fit()
        alpha0 = lm.params.loc['Intercept']
        alph = lm.params.loc['X'] 

        lm = smf.ols(formula='Y ~ z + X', data=df).fit()
        beta0 = lm.params.Intercept 
        bet = lm.params.z
        gam = lm.params.X 
        resid_std = np.std(lm.resid)
        e = df.Y - beta0 - (df.X*gam)
        h = alpha0 + df.X*alph
        d = (((bet*e)+h)/((bet**2)+1))
        
        if tune:
            if algo== 'svr':
                model = auxiliaryfunctions.get_svr_model(M,d)
                z = model.predict(M)
            else:
                adam = Adam()
                model.compile(loss='mean_absolute_error',optimizer=adam)
                if early_stopping:
                    es = EarlyStopping(monitor='val_loss', mode='min', verbose=1,patience=20)
                    history = model.fit(M,d,batch_size=batch_size,epochs=epochs,verbose=1,callbacks=[es],
                                      shuffle=True,validation_split = 0.3)
                else:
                    history = model.fit(M,d,batch_size=batch_size,epochs=epochs,verbose=1,
                                  shuffle=True,validation_split = 0.3)
                z = model.predict(M)
       
        params_df.loc[n_runs]['alpha0','iter_'+str(i)]=alpha0
        params_df.loc[n_runs]['beta0','iter_'+str(i)]=beta0
        params_df.loc[n_runs]['beta','iter_'+str(i)]=bet
        params_df.loc[n_runs]['gamma','iter_'+str(i)]=gam
        params_df.loc[n_runs]['alpha','iter_'+str(i)]=alph

        try:
            z = np.concatenate(z)
        except:
            pass
       
    return params_df,z


In [4]:
os.environ["CUDA_VISIBLE_DEVICES"]="0"
for n in num_subs:
    start = 0
    output_df = create_empty_df(num_runs,num_iters)
    for runs in range(start,num_runs):
        K.clear_session()
        print("*****************Running simulation for num subs %s starting with %s runs*****************"%(n,runs+1))
    # simulate the dataset
        df,mediator,z = auxiliaryfunctions.simulate_dataset(n,resize= True,
                                          new_shape=new_shape,visualize=False,algo=algo,alpha=0)
    # create a model 
        if algo == 'svr':
            model = auxiliaryfunctions.create_svr_model(mediator,df.m)
        elif algo== 'shallow':
            input_shape = (new_shape[0],new_shape[1]*4,1)
            model = auxiliaryfunctions.create_shallow_model2D(input_shape=input_shape)
        else:
            print('Using deep network...')
            input_shape = (new_shape[0],new_shape[1]*4,1)
            model = auxiliaryfunctions.create_deep_model2D(input_shape=input_shape)

        params_df,z_final = simulate_mediation(df,mediator,output_df,model,algo,n,batch_size,epochs,
                                      True,n,runs,num_iters)
        params_df.to_excel(os.path.join(result_path,'simulation-3-num-subs-'+str(n)+'-'+algo+'.xlsx'))

*****************Running simulation for num subs 1000 starting with 1 runs*****************
Using deep network...
Using intial random model parameters
Starting iteration... 1
Epoch 1/1000
175/175 [==============================] - 2s 10ms/step - loss: 36.5037 - val_loss: 0.8667
Epoch 2/1000
175/175 [==============================] - 1s 7ms/step - loss: 2.0071 - val_loss: 0.8543
Epoch 3/1000
175/175 [==============================] - 1s 7ms/step - loss: 1.8842 - val_loss: 0.8600
Epoch 4/1000
175/175 [==============================] - 1s 7ms/step - loss: 1.8800 - val_loss: 0.8552
Epoch 5/1000
175/175 [==============================] - 1s 7ms/step - loss: 1.8756 - val_loss: 0.8555
Epoch 6/1000
175/175 [==============================] - 1s 7ms/step - loss: 1.8299 - val_loss: 0.8512
Epoch 7/1000
175/175 [==============================] - 1s 7ms/step - loss: 1.7486 - val_loss: 0.8453
Epoch 8/1000
175/175 [==============================] - 1s 7ms/step - loss: 1.6986 - val_loss: 0.8482
Epoch 9

Epoch 79/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4893 - val_loss: 0.2829
Epoch 80/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4807 - val_loss: 0.2906
Epoch 81/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4956 - val_loss: 0.2753
Epoch 82/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4781 - val_loss: 0.2937
Epoch 83/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4891 - val_loss: 0.2892
Epoch 84/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4793 - val_loss: 0.3015
Epoch 85/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4673 - val_loss: 0.2933
Epoch 86/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4557 - val_loss: 0.2787
Epoch 87/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4607 - val_loss: 0.2787
Epoch 88/1000
175/175 [==============================] - 1s 7ms/step - lo

Epoch 34/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.6022 - val_loss: 0.4618
Epoch 35/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5849 - val_loss: 0.4472
Epoch 36/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5684 - val_loss: 0.4192
Epoch 37/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5544 - val_loss: 0.3863
Epoch 38/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5699 - val_loss: 0.3840
Epoch 39/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5175 - val_loss: 0.3782
Epoch 40/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5200 - val_loss: 0.3663
Epoch 41/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5173 - val_loss: 0.3572
Epoch 42/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5046 - val_loss: 0.3288
Epoch 43/1000
175/175 [==============================] - 1s 7ms/step - lo

175/175 [==============================] - 1s 7ms/step - loss: 0.4192 - val_loss: 0.2640
Epoch 17/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3991 - val_loss: 0.2704
Epoch 18/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4247 - val_loss: 0.2651
Epoch 19/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4030 - val_loss: 0.2739
Epoch 20/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3880 - val_loss: 0.2575
Epoch 21/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.4034 - val_loss: 0.2634
Epoch 22/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3872 - val_loss: 0.2580
Epoch 23/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3850 - val_loss: 0.2647
Epoch 24/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3843 - val_loss: 0.2619
Epoch 25/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3717 - v

175/175 [==============================] - 1s 8ms/step - loss: 0.8504 - val_loss: 0.7846
Epoch 6/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.8243 - val_loss: 0.7494
Epoch 7/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.7990 - val_loss: 0.6787
Epoch 8/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.7459 - val_loss: 0.5849
Epoch 9/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.6338 - val_loss: 0.4265
Epoch 10/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5852 - val_loss: 0.4123
Epoch 11/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5459 - val_loss: 0.4173
Epoch 12/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5445 - val_loss: 0.3722
Epoch 13/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5355 - val_loss: 0.3184
Epoch 14/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.5150 - val_l

...

175/175 [==============================] - 1s 7ms/step - loss: 0.7615 - val_loss: 0.5199
Epoch 126/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.7466 - val_loss: 0.5063
Epoch 127/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.7564 - val_loss: 0.5242
Epoch 128/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.7317 - val_loss: 0.5208
Epoch 129/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.7314 - val_loss: 0.5081
Epoch 130/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.7030 - val_loss: 0.4788
Epoch 131/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.6953 - val_loss: 0.4956
Epoch 132/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.7043 - val_loss: 0.4562
Epoch 133/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.7173 - val_loss: 0.4542
Epoch 134/1000
175/175 [==============================] - 1s 7ms/step - loss: 0

Epoch 204/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3729 - val_loss: 0.2713
Epoch 205/1000
175/175 [==============================] - 1s 8ms/step - loss: 0.3578 - val_loss: 0.2609
Epoch 206/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3606 - val_loss: 0.2946
Epoch 207/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3755 - val_loss: 0.2669
Epoch 208/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3446 - val_loss: 0.2604
Epoch 209/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3663 - val_loss: 0.2643
Epoch 210/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3693 - val_loss: 0.2672
Epoch 211/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3740 - val_loss: 0.2620
Epoch 212/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3543 - val_loss: 0.2611
Epoch 213/1000
175/175 [==============================] - 1s 7ms

Epoch 283/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3202 - val_loss: 0.2439
Epoch 284/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3234 - val_loss: 0.2494
Epoch 285/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3164 - val_loss: 0.2476
Epoch 286/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3138 - val_loss: 0.2482
Epoch 287/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3290 - val_loss: 0.2527
Epoch 288/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3178 - val_loss: 0.2461
Epoch 289/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3314 - val_loss: 0.2486
Epoch 290/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3174 - val_loss: 0.2443
Epoch 291/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3165 - val_loss: 0.2436
Epoch 292/1000
175/175 [==============================] - 1s 7ms

Epoch 46/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3639 - val_loss: 0.2866
Epoch 47/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3584 - val_loss: 0.2809
Epoch 48/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3500 - val_loss: 0.2591
Epoch 49/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3596 - val_loss: 0.2693
Epoch 50/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3563 - val_loss: 0.2713
Epoch 51/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3513 - val_loss: 0.2668
Epoch 52/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3575 - val_loss: 0.2734
Epoch 53/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3634 - val_loss: 0.2656
Epoch 54/1000
175/175 [==============================] - 1s 7ms/step - loss: 0.3605 - val_loss: 0.2576
Epoch 55/1000
175/175 [==============================] - 1s 7ms/step - lo

KeyboardInterrupt: 